In [1]:
import sys, os 
sys.path.append('/home/monte.flora/python_packages/frdd-wofs-cast/')

from wofscast import data_utils
from wofscast.wofscast_task_config import WOFS_TASK_CONFIG, train_lead_times
from wofscast.data_generator import to_static_vars, add_local_solar_time, load_wofscast_data

import xarray as xr
from glob import glob
import numpy as np
import dataclasses
import random 

import dask 
from dask.diagnostics import ProgressBar
from dask.distributed import Client
import logging

import random
from collections import defaultdict

In [2]:
def check_for_nans(dataset):

    # Iterate through each variable in the Dataset
    for var_name, data_array in dataset.items():
        # Find boolean mask of NaNs
        nan_mask = data_array.isnull()
    
        # Use np.where to find the indices of NaNs
        nan_indices = np.where(nan_mask)
    
        # `nan_indices` is a tuple of arrays, each array corresponds to indices along one dimension
        # Print the locations of NaNs
        print(f"NaN locations in {var_name}:")
        for dim, inds in zip(nan_mask.dims, nan_indices):
            print(f"  {dim}: {inds}")   

In [3]:
client = Client(n_workers=40, threads_per_worker=1, memory_limit=0, silence_logs=logging.ERROR)
client

<Client: 'tcp://127.0.0.1:42843' processes=40 threads=40>

### Check for consistent time dimension (ran once and all files passed!)

### Randomly sample the different cases and ensemble members to improve training dataset diversity 

In [4]:
data_paths = []
# Only doing 2019 and 2020 and leaving 2021 as the evaluation dataset?
for year in ['2019', '2020']:
    data_paths.extend(glob(os.path.join(f'/work/mflora/wofs-cast-data/datasets/{year}/wrf*.nc')))

# Function to parse date and ensemble member from a file name
def parse_file_info(file_name):
    parts = file_name.split('_')
    date = parts[1]
    ens_mem = parts[-1].split('.')[0]
    return date, ens_mem

# Organize files by date and ensemble member
files_by_date_and_ens = defaultdict(lambda: defaultdict(list))
for file_path in data_paths:
    file_name = os.path.basename(file_path)
    date, ens_mem = parse_file_info(file_name)
    files_by_date_and_ens[date][ens_mem].append(file_path)

# Decide how many samples you want per date and ensemble member
samples_per_date_and_ens = 1  # Example: 1 sample per combination

# Sample files
sampled_files = []
for date, ens_members in files_by_date_and_ens.items():
    for ens_mem, files in ens_members.items():
        if len(files) >= samples_per_date_and_ens:
            sampled_files.extend(random.sample(files, samples_per_date_and_ens))
        else:
            sampled_files.extend(files)  # Add all if fewer files than desired samples

# sampled_files now contains your randomly sampled files
print(len(sampled_files))

1620


In [5]:
%%time

inputs, targets, forcings = load_wofscast_data(sampled_files, 
                                               train_lead_times, 
                                               WOFS_TASK_CONFIG, client)

# Load all the data into memory. 
#dataset = xr.open_mfdataset(data_paths, 
#                                concat_dim='batch', 
#                                parallel=True, 
#                                combine='nested',
#                                preprocess=add_local_solar_time
#                                    ) 
    
#inputs, targets, forcings = data_utils.extract_inputs_targets_forcings(dataset,
#                                                        target_lead_times=train_lead_times,
#                                                        **dataclasses.asdict(TASK_WOFS))

/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:3162: UserWarning: Sending large graph of size 12.14 MiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(
Process Dask Worker process (from Nanny):
2024-03-21 18:24:04,172 - distributed.nanny - ERROR - Worker process died unexpectedly
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/nanny.py", line 1021, in _run
    asyncio_run(run(), loop_factory=get_loop_factory())
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 239, in asyncio_run
    _cancel_all_tasks(loop)
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 255, in _cancel_all_tasks
    loop.run_until_complete(asyncio.gather(*to_cancel, return_exceptions=True))
  File "/work/mflora/miniconda3

In [6]:
print('Train Input Dims: ', inputs.dims.mapping)
print('Train Target Dims: ', targets.dims.mapping)
print('Train Forcing Dims: ', forcings.dims.mapping)

Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
2024-03-21 18:24:05,039 - distributed.nanny - ERROR - Worker process died unexpectedly
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
2024-03-21 18:24:05,039 - distributed.nanny - ERROR - Worker process died unexpectedly
Process Dask Worker process (from Nanny):
Process Dask Worker process (from Nanny):
2024-03-21 18:24:05,039 - distributed.nanny - ERROR - Worker process died unexpectedly
2024-03-21 18:24:05,039 - distributed.nanny - ERROR - Worker process died unexpectedly
2024-03-21 18:24:05,039 - distributed.nanny - ERROR - Worker process died unexpectedly
Process Dask Worker process (from Nanny):
Process Dask Worker

  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 1871, in _run_once
    event_list = self._selector.select(timeout)
Traceback (most recent call last):
KeyboardInterrupt
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 1871, in _run_once
    event_list = self._selector.select(timeout)
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 236, in asyncio_run
    return loop.run_until_complete(main)
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 236, in asyncio_run
    return loop.run_until_complete(main)
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 255, in _cancel_all_tasks
    loop.run_until_complete(asyncio.gather(*to_cancel, return_exceptions=True))
Traceback (most recent call last):
  File "/work/mflora/miniconda

In [ ]:
for ds in [inputs, targets, forcings]: 
    check_for_nans(ds)

lib/python3.10/asyncio/base_events.py", line 636, in run_until_complete
    self.run_forever()
KeyboardInterrupt
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 236, in asyncio_run
    return loop.run_until_complete(main)
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 636, in run_until_complete
    self.run_forever()
Traceback (most recent call last):
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 636, in run_until_complete
    self.run_forever()
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 636, in run_until_complete
    self.run_forever()
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 236, in asyncio_run
    return loop.run_until_complete(main)
  File "/work/mflora/miniconda3/envs/wofs-cas

In [ ]:
# Calculate the memory usage in bytes
memory_usage_bytes = targets.nbytes + inputs.nbytes + forcings.nbytes

# Alternatively, for gigabytes (GB)
memory_usage_gb = memory_usage_bytes / (1024**3)
print(f"Total Memory Usage for Inputs, Targets, and Forcings: {memory_usage_gb:.2f} GB")

t/lib/python3.10/asyncio/base_events.py", line 603, in run_forever
    self._run_once()
2024-03-21 18:24:05,040 - distributed.nanny - ERROR - Worker process died unexpectedly
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 603, in run_forever
    self._run_once()
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 603, in run_forever
    self._run_once()

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/compatibility.py", line 236, in asyncio_run
    return loop.run_until_complete(main)
Traceback (most recent call last):
KeyboardInterrupt
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 603, in run_forever
    self._run_once()
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/asyncio/base_events.py", line 603

In [ ]:
out_path = '/work/mflora/wofs-cast-data/train_datasets'
inputs.to_netcdf(os.path.join(out_path, 'train_inputs.nc'))
targets.to_netcdf(os.path.join(out_path, 'train_targets.nc'))
forcings.to_netcdf(os.path.join(out_path, 'train_forcings.nc'))

In [7]:
import gc
client.close()
gc.collect()

Task exception was never retrieved
future: <Task finished name='Task-105631' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-104108' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-104113' coro=<Client._gather.<loc

Task exception was never retrieved
future: <Task finished name='Task-104128' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-104123' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-104124' coro=<Client._gather.<loc

Task exception was never retrieved
future: <Task finished name='Task-92975' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-92979' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-92964' coro=<Client._gather.<locals

Task exception was never retrieved
future: <Task finished name='Task-92945' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-92941' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-92937' coro=<Client._gather.<locals

Task exception was never retrieved
future: <Task finished name='Task-92919' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-92893' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-92888' coro=<Client._gather.<locals

...

Task exception was never retrieved
future: <Task finished name='Task-84066' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-84085' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-84065' coro=<Client._gather.<locals

Task exception was never retrieved
future: <Task finished name='Task-83971' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-83977' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-83980' coro=<Client._gather.<locals

Task exception was never retrieved
future: <Task finished name='Task-83854' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-83828' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-83826' coro=<Client._gather.<locals

Task exception was never retrieved
future: <Task finished name='Task-78279' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-78277' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-78270' coro=<Client._gather.<locals

Task exception was never retrieved
future: <Task finished name='Task-78235' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-78234' coro=<Client._gather.<locals>.wait() done, defined at /work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py:2208> exception=AllExit()>
Traceback (most recent call last):
  File "/work/mflora/miniconda3/envs/wofs-cast/lib/python3.10/site-packages/distributed/client.py", line 2217, in wait
    raise AllExit()
distributed.client.AllExit
Task exception was never retrieved
future: <Task finished name='Task-78133' coro=<Client._gather.<locals